# Exploring Philadelphia Energy Burdens

## Setting up

In [4]:
import pandas as pd
import geopandas as gpd
import numpy as np
import cenpy
import carto2gpd

import holoviews as hv
import hvplot.pandas
hv.extension('bokeh')
import param as pm
import panel as pn
pn.extension()
import hvplot
import folium
from folium.plugins import MarkerCluster
from geopy.geocoders import Nominatim
from pylab import *

import altair as alt
import folium
from folium.plugins import HeatMap

pd.options.display.max_rows = 9999 
pd.options.display.max_colwidth = 200

## Data collection

In [5]:
acs = cenpy.remote.APIConnection("ACSDT5Y2020")

In [6]:
variables = [
    "NAME",
    "B02001_001E",
    "B02001_002E",
    "B02001_003E",
    "B02001_004E",
    "B02001_005E",
    "B02001_006E",
    "B02001_007E",
    "B25040_002E",
    "B25040_003E",
    "B25040_004E",
    "B25040_005E",
    "B25040_006E",
    "B25040_007E",
    "B25040_008E",
    "B25040_009E",
    "B25069_002E",
    "B25069_003E",
    "B25071_001E",
    "B25105_001E",
    "B25002_001E",
    "B25002_002E",
    "B25002_003E",
    "B25003_001E",
    "B25003_002E",
    "B25003_003E",
    "B25024_001E",
    "B25024_006E",
    "B25024_007E",
    "B25024_008E",
    "B25024_009E",
]

In [7]:
philly_county_code = "101"
pa_state_code = "42"

philly_census = acs.query(
    cols=variables,
    geo_unit="tract",
    geo_filter={"state": pa_state_code, 
                "county": philly_county_code},
)


## Data cleaning

In [8]:
for variable in variables:
    if variable != "NAME":
        philly_census[variable] = philly_census[variable].astype(float)

In [9]:
philly_census_final = philly_census.rename(
    columns={
        "B02001_001E": "Total_Population",
        "B02001_002E": "White",
        "B02001_003E": "Black",
        "B02001_004E": "American Indian",
        "B02001_005E": "Asian",
        "B02001_006E": "Native Hawaiian, Other Pacific Islander",
        "B02001_007E": "Other Race",
        "B25040_002E": "Gas",
        "B25040_003E": "Bottled Tank Gas",
        "B25040_004E": "Electricity",
        "B25040_005E": "Fuel Oil",
        "B25040_006E": "Coal",
        "B25040_007E": "Wood",
        "B25040_008E": "Solar Energy",
        "B25040_009E": "Other Fuel",
        "B25069_002E": "Extra Payment Utilities",
        "B25069_003E": "No Extra Payment",
        "B25071_001E": "Rent_as_%_of_Income",
        "B25105_001E": "MedianMonthlyHousingCosts",
        "B25002_001E": "Occ Total Units",
        "B25002_002E": "Occ Total Occupied",
        "B25002_003E": "Occ Total Vacant",
        "B25003_001E": "Tenure Total Units",
        "B25003_002E": "Owner-Occupied",
        "B25003_003E": "Renter-Occupied",
        "B25024_001E": "Total Units",
        "B25024_006E": "Units 5-9",
        "B25024_007E": "Units 10-19",
        "B25024_008E": "Units 20-49",
        "B25024_009E": "Units 50+",
    }
)

In [10]:
EnergyCosts = pd.read_csv("C:/Users/admin/Documents/GitHub/final-project-philly-energy-burden/Data/LEAD avg energy costs.csv")
BurdenCounts = pd.read_csv("C:/Users/admin/Documents/GitHub/final-project-philly-energy-burden/Data/LEAD housing counts.csv")
EnergyBurden = pd.read_csv("C:/Users/admin/Documents/GitHub/final-project-philly-energy-burden/Data/LEAD avg energy burden.csv")
CensusTracts = gpd.read_file("C:/Users/admin/Documents/GitHub/final-project-philly-energy-burden/Data/Census_Tracts_2010 (4).geojson")

In [11]:
philly_census_final['GEOID10'] = philly_census_final['state'] + philly_census_final['county'] + philly_census_final['tract'].astype(str)
BurdenCounts = BurdenCounts.rename(
    columns={
        "Geography ID": "GEOID10",
        "Housing Counts": "HouseholdCount"}
)
EnergyCosts = EnergyCosts.rename(
    columns={
        "Geography ID": "GEOID10",
        "Avg. Annual Energy Cost": "AvgAnnualEnergyCost"}
)
EnergyBurden = EnergyBurden.rename(
    columns={
        "Geography ID": "GEOID10",
        "Avg. Energy Burden (% income)": "EnergyBurden"}
)


philly_census_final

NAME  \
0      Census Tract 27.01, Philadelphia County, Pennsylvania   
1      Census Tract 27.02, Philadelphia County, Pennsylvania   
2      Census Tract 28.01, Philadelphia County, Pennsylvania   
3      Census Tract 28.02, Philadelphia County, Pennsylvania   
4         Census Tract 29, Philadelphia County, Pennsylvania   
5      Census Tract 30.01, Philadelphia County, Pennsylvania   
6      Census Tract 30.02, Philadelphia County, Pennsylvania   
7         Census Tract 31, Philadelphia County, Pennsylvania   
8         Census Tract 32, Philadelphia County, Pennsylvania   
9         Census Tract 33, Philadelphia County, Pennsylvania   
10        Census Tract 36, Philadelphia County, Pennsylvania   
11     Census Tract 37.01, Philadelphia County, Pennsylvania   
12     Census Tract 37.02, Philadelphia County, Pennsylvania   
13        Census Tract 38, Philadelphia County, Pennsylvania   
14     Census Tract 39.01, Philadelphia County, Pennsylvania   
15     Census Tract 39.02, Philadelphia County, Pennsylvania   
16     Census Tract 40.01, Philadelphia County, Pennsylvania   
17     Census Tract 40.02, Philadelphia County, Pennsylvania   
18     Census Tract 41.01, Philadelphia County, Pennsylvania   
19     Census Tract 41.03, Philadelphia County, Pennsylvania   
20     Census Tract 41.04, Philadelphia County, Pennsylvania   
21     Census Tract 42.01, Philadelphia County, Pennsylvania   
22     Census Tract 42.02, Philadelphia County, Pennsylvania   
23        Census Tract 54, Philadelphia County, Pennsylvania   
24        Census Tract 55, Philadelphia County, Pennsylvania   
25        Census Tract 56, Philadelphia County, Pennsylvania   
26        Census Tract 60, Philadelphia County, Pennsylvania   
27        Census Tract 61, Philadelphia County, Pennsylvania   
28        Census Tract 62, Philadelphia County, Pennsylvania   
29        Census Tract 63, Philadelphia County, Pennsylvania   
30        Census Tract 64, Philadelphia County, Pennsylvania   
31        Census Tract 65, Philadelphia County, Pennsylvania   
32        Census Tract 66, Philadelphia County, Pennsylvania   
33        Census Tract 67, Philadelphia County, Pennsylvania   
34        Census Tract 70, Philadelphia County, Pennsylvania   
35     Census Tract 71.01, Philadelphia County, Pennsylvania   
36     Census Tract 71.02, Philadelphia County, Pennsylvania   
37        Census Tract 72, Philadelphia County, Pennsylvania   
38        Census Tract 73, Philadelphia County, Pennsylvania   
39        Census Tract 74, Philadelphia County, Pennsylvania   
40        Census Tract 77, Philadelphia County, Pennsylvania   
41        Census Tract 78, Philadelphia County, Pennsylvania   
42        Census Tract 79, Philadelphia County, Pennsylvania   
43        Census Tract 80, Philadelphia County, Pennsylvania   
44     Census Tract 81.01, Philadelphia County, Pennsylvania   
45     Census Tract 81.02, Philadelphia County, Pennsylvania   
46        Census Tract 82, Philadelphia County, Pennsylvania   
47     Census Tract 83.01, Philadelphia County, Pennsylvania   
48     Census Tract 83.02, Philadelphia County, Pennsylvania   
49        Census Tract 84, Philadelphia County, Pennsylvania   
50        Census Tract 85, Philadelphia County, Pennsylvania   
51     Census Tract 86.01, Philadelphia County, Pennsylvania   
52     Census Tract 86.02, Philadelphia County, Pennsylvania   
53     Census Tract 87.01, Philadelphia County, Pennsylvania   
54     Census Tract 87.02, Philadelphia County, Pennsylvania   
55     Census Tract 88.01, Philadelphia County, Pennsylvania   
56     Census Tract 88.02, Philadelphia County, Pennsylvania   
57        Census Tract 90, Philadelphia County, Pennsylvania   
58        Census Tract 91, Philadelphia County, Pennsylvania   
59        Census Tract 92, Philadelphia County, Pennsylvania   
60        Census Tract 93, Philadelphia County, Pennsylvania   
61        Census Tract 94, Philadelphia County, Pennsylvania   
62        Census Tract 9

In [14]:
join = CensusTracts.merge(philly_census_final, on="GEOID10")
LEAD = EnergyBurden.merge(EnergyCosts, on="GEOID10")
AllLead = LEAD.merge(BurdenCounts, on='GEOID10')
alldata = pd.concat([join, AllLead], axis=1, join='inner')
cols = [1,2,3,4,5,6,7,8,9,10,11,12,13,33,46,47,48,49,50,51,52,54,55,56,58,59,60]
finaldata = alldata.drop(alldata.columns[cols],axis=1,inplace=False)
finaldata = finaldata.apply(pd.to_numeric, errors='ignore')
finaldata

OBJECTID  \
0           1   
1           2   
2           3   
3           4   
4           5   
5           6   
6           7   
7           9   
8          10   
9          11   
10         12   
11         13   
12         14   
13         15   
14         16   
15         17   
16         18   
17         19   
18         20   
19         21   
20         22   
21         23   
22         24   
23         25   
24         26   
25         27   
26         28   
27         29   
28         30   
29         32   
30         33   
31         34   
32         35   
33         36   
34         37   
35         38   
36         39   
37         40   
38         41   
39         42   
40         43   
41         44   
42         45   
43         47   
44         48   
45         49   
46         50   
47         51   
48         52   
49         53   
50         54   
51         55   
52         56   
53         57   
54         58   
55         59   
56         60   
57         61   
58         62   
59         63   
60         64   
61         65   
62         66   
63         67   
64         68   
65         69   
66         70   
67         72   
68         73   
69         74   
70         75   
71         76   
72         77   
73         78   
74         79   
75         80   
76         81   
77         83   
78         84   
79         85   
80         86   
81         87   
82         88   
83         89   
84         90   
85         91   
86         92   
87         93   
88         94   
89         95   
90         96   
91         97   
92         98   
93         99   
94        100   
95        101   
96        102   
97        103   
98        104   
99        105   
100       106   
101       107   
102       108   
103       109   
104       110   
105       111   
106       112   
107       113   
108       114   
109       115   
110       116   
111       117   
112       118   
113       119   
114       120   
115       121   
116       122   
117       123   
118       124   
119       125   
120       126   
121       127   
122       128   
123       129   
124       130   
125       131   
126       132   
127       133   
128       134   
129       135   
130       136   
131       137   
132       138   
133       139   
134       140   
135       141   
136       142   
137       143   
138       145   
139       146   
140       147   
141       148   
142       149   
143       150   
144       151   
145       152   
146       153   
147       154   
148       155   
149       156   
150       157   
151       158   
152       159   
153       160   
154       161   
155       162   
156       163   
157       164   
158       165   
159       166   
160       167   
161       168   
162       169   
163       170   
164       171   
165       172   
166       173   
167       174   
168       175   
169       176   
170       177   
171       178   
172       179   
173       180   
174       181   
175       182   
176       183   
177       184   
178       185   
179       186   
180       187   
181       188   
182       189   
183       191   
184       192   
185       193   
186       194   
187       196   
188       197   
189       198   
190       199   
191       200   
192       201   
193       202   
194       203   
195       204   
196       206   
197       207   
198       208   
199       209   
200       210   
201       211   
202       212   
203       213   
204       214   
205       215   
206       216   
207       217   
208       218   
209       219   
210       221   
211       222   
212       223   
213       224   
214       225   
215       226   
216       227   
217       228   
218       229   
219       230   
220       231   
221       232   
222       234   
223       235   
224       236   
225       237   
226       239   
227       240   
228       241   
229       242   
230       243   
231       244   
232       245   
233       246   
234       

In [15]:
variables2 = [
    "NAME",
    "B19013_001E",
]

philly_census2 = acs.query(
    cols=variables2,
    geo_unit="tract",
    geo_filter={"state": pa_state_code, 
                "county": philly_county_code},
)
philly_census2_final = philly_census2.rename(
    columns={
        "B19013_001E": "MedianIncome"})
    
philly_census2_final

NAME MedianIncome  \
0      Census Tract 27.01, Philadelphia County, Pennsylvania        80470   
1      Census Tract 27.02, Philadelphia County, Pennsylvania        76060   
2      Census Tract 28.01, Philadelphia County, Pennsylvania        65847   
3      Census Tract 28.02, Philadelphia County, Pennsylvania        67585   
4         Census Tract 29, Philadelphia County, Pennsylvania        66932   
5      Census Tract 30.01, Philadelphia County, Pennsylvania        50536   
6      Census Tract 30.02, Philadelphia County, Pennsylvania        54286   
7         Census Tract 31, Philadelphia County, Pennsylvania        57250   
8         Census Tract 32, Philadelphia County, Pennsylvania        43289   
9         Census Tract 33, Philadelphia County, Pennsylvania        53678   
10        Census Tract 36, Philadelphia County, Pennsylvania        36861   
11     Census Tract 37.01, Philadelphia County, Pennsylvania        39340   
12     Census Tract 37.02, Philadelphia County, Pennsylvania        40202   
13        Census Tract 38, Philadelphia County, Pennsylvania        75682   
14     Census Tract 39.01, Philadelphia County, Pennsylvania        51932   
15     Census Tract 39.02, Philadelphia County, Pennsylvania        66179   
16     Census Tract 40.01, Philadelphia County, Pennsylvania        61542   
17     Census Tract 40.02, Philadelphia County, Pennsylvania        63726   
18     Census Tract 41.01, Philadelphia County, Pennsylvania        36365   
19     Census Tract 41.03, Philadelphia County, Pennsylvania        47905   
20     Census Tract 41.04, Philadelphia County, Pennsylvania        47409   
21     Census Tract 42.01, Philadelphia County, Pennsylvania        61633   
22     Census Tract 42.02, Philadelphia County, Pennsylvania        61858   
23        Census Tract 54, Philadelphia County, Pennsylvania        57333   
24        Census Tract 55, Philadelphia County, Pennsylvania        61417   
25        Census Tract 56, Philadelphia County, Pennsylvania        42031   
26        Census Tract 60, Philadelphia County, Pennsylvania        43235   
27        Census Tract 61, Philadelphia County, Pennsylvania        35361   
28        Census Tract 62, Philadelphia County, Pennsylvania        32521   
29        Census Tract 63, Philadelphia County, Pennsylvania        28681   
30        Census Tract 64, Philadelphia County, Pennsylvania        28981   
31        Census Tract 65, Philadelphia County, Pennsylvania        36974   
32        Census Tract 66, Philadelphia County, Pennsylvania        21289   
33        Census Tract 67, Philadelphia County, Pennsylvania        37056   
34        Census Tract 70, Philadelphia County, Pennsylvania        38378   
35     Census Tract 71.01, Philadelphia County, Pennsylvania        34303   
36     Census Tract 71.02, Philadelphia County, Pennsylvania        29738   
37        Census Tract 72, Philadelphia County, Pennsylvania        35412   
38        Census Tract 73, Philadelphia County, Pennsylvania        32195   
39        Census Tract 74, Philadelphia County, Pennsylvania        33424   
40        Census Tract 77, Philadelphia County, Pennsylvania        50625   
41        Census Tract 78, Philadelphia County, Pennsylvania        49526   
42        Census Tract 79, Philadelphia County, Pennsylvania        66667   
43        Census Tract 80, Philadelphia County, Pennsylvania        60163   
44     Census Tract 81.01, Philadelphia County, Pennsylvania        41537   
45     Census Tract 81.02, Philadelphia County, Pennsylvania        39157   
46        Census Tract 82, Philadelphia County, Pennsylvania        30182   
47     Census Tract 83.01, Philadelphia County, Pennsylvania        33478   
48     Census Tract 83.02, Philadelphia County, Pennsylvania        24497   
49        Census Tract 84, Philadelphia County, Pennsylvania        43839   
50        Census Tract 85, Philadelphia County, Pennsylvania        38610   
51     Census Tract 86.01, Philadelphia County, Penn

In [23]:
finaldata['Rent%Income'] = philly_census_final['Rent_as_%_of_Income']
finaldata['GEOID'] = philly_census_final['GEOID10']
finaldata['Race'] = finaldata[['White','Black', 'American Indian', 'Asian', 'Native Hawaiian, Other Pacific Islander', 'Other Race']].idxmax(axis=1)
finaldata['Occupancy'] = finaldata[['Owner-Occupied', 'Renter-Occupied']].idxmax(axis=1)
finaldata['SFCount'] = (finaldata['Total Units'] - (finaldata['Units 5-9'] + finaldata['Units 10-19'] + finaldata['Units 20-49'] + finaldata['Units 50+']))
finaldata['Housing_type'] = finaldata[['SFCount','Units 5-9', 'Units 20-49', 'Units 50+']].idxmax(axis=1)
finaldata['Housing'] = np.where(finaldata['Housing_type'] == 'SFCount', 'Single Family', 'Multifamily')
finaldata['Fuel'] = finaldata[['Gas', 'Bottled Tank Gas', 'Electricity', 'Fuel Oil', 'Coal', 'Wood', 'Solar Energy', 'Other Fuel']].idxmax(axis=1)
finaldata['Utilities'] = finaldata[['Extra Payment Utilities', 'No Extra Payment']].idxmax(axis=1)
finaldata['MedIncome'] = philly_census2_final['MedianIncome']
finaldata['IncomeLevel'] = np.where(finaldata['MedIncome'] > '94500', 'Above AMI', 'Below AMI')
cols2 = [4,5,6,7,8,9,10,11,12,13,14,15,16,17,18,19,21,22,23,24,25,25,26,27,28,29,30,31,39,40]
Data = finaldata.drop(finaldata.columns[cols2],axis=1,inplace=False)
Data = Data.apply(pd.to_numeric, errors='ignore')

## Creating dashboard elements

In [24]:
pn.extension(sizing_mode='fixed')
Burden = pn.widgets.IntSlider(name='Energy Burden (% of Income) Slider', width = 200, start = 1, end =10, value = (5), step=1, value_throttled= (3))

In [25]:
@pn.depends(Burden.param.value_throttled)
def Burden_selected(Burden):
    return 'Average Energy Burden = {}'.format(Burden)

In [26]:
class EnergyBurdenByTract(pm.Parameterized):
    pn.extension(sizing_mode='fixed')
    Burden = pn.widgets.IntSlider(name='Energy Burden (% of Income) Slider', width = 200, start = 1, end =10, value = (5), step=1, value_throttled= (3))

In [27]:
def choropleth():
        columns2 = ["GEOID", "NAME", "geometry", "EnergyBurden","HouseholdCount","MedianMonthlyHousingCosts", "AvgAnnualEnergyCost","Rent%Income"]
        return Data[columns2].hvplot.polygons(
            c="EnergyBurden",
            legend=True,
            cmap="viridis",
            hover_cols=["NAME", "GEOID", "EnergyBurden", "HouseholdCount", "MedianMonthlyHousingCosts", "AvgAnnualEnergyCost", "Rent%Income"],
            frame_width=550,
            frame_height=600,
            geo=True,
            crs=3857,
            title="Average Energy Burden by Census Tracts"
        )

In [28]:
@pn.depends(Burden.param.value_throttled)
def Burden_selected(Burden):
        return 'Average Energy Burden = {}'.format(Burden)


In [29]:
@pn.depends(Burden.param.value_throttled)
def plot_bar1(Burden):
        Burden_df = Data[Data['EnergyBurden'] == Burden]
        df = pd.DataFrame(Burden_df.groupby('Race')[['Race','OBJECTID']]
                      .count()['OBJECTID'])
        df['Race'] = df.index
        return df.hvplot.bar(x='Race', y='OBJECTID', c='Race', cmap='viridis', min_height=300, min_width=500, legend=False, yformatter='%.0f', responsive=True).opts(xlabel="Most Common Race in Census Tract", ylabel="Tracts with Specified Energy Burden", title= "Energy Burden by Race")

   

In [30]:
@pn.depends(Burden.param.value_throttled)
def plot_bar2(Burden):
        Burden_df = Data[Data['EnergyBurden'] == Burden]
        df = pd.DataFrame(Burden_df.groupby('Housing')[['Housing','OBJECTID']]
                      .count()['OBJECTID'])
        df['Housing'] = df.index
        return df.hvplot.bar(x='Housing', y='OBJECTID', c='Housing', cmap='viridis', min_height=300, min_width=500, legend=False, yformatter='%.0f', responsive=True).opts(xlabel="Most Common Housing Type in Census Tract", ylabel="Tracts with Specified Energy Burden", title= "Energy Burden by Housing Type")

   

In [31]:
@pn.depends(Burden.param.value_throttled)
def plot_bar3(Burden):
        Burden_df = Data[Data['EnergyBurden'] == Burden]
        df = pd.DataFrame(Burden_df.groupby('Occupancy')[['Occupancy','OBJECTID']]
                        .count()['OBJECTID'])
        df['Occupancy'] = df.index
        return df.hvplot.bar(x='Occupancy', y='OBJECTID', c='Occupancy', cmap='viridis', min_height=300, min_width=500, legend=False, yformatter='%.0f', responsive=True).opts(xlabel="Most Common Occupancy Type in Census Tract", ylabel="Tracts with Specified Energy Burden", title= "Energy Burden by Occupancy Type")

    

In [32]:
@pn.depends(Burden.param.value_throttled)
def plot_bar4(Burden):
        Burden_df = Data[Data['EnergyBurden'] == Burden]
        df = pd.DataFrame(Burden_df.groupby('Fuel')[['Fuel','OBJECTID']]
                      .count()['OBJECTID'])
        df['Fuel'] = df.index
        return df.hvplot.bar(x='Fuel', y='OBJECTID', c='Fuel', cmap='viridis', min_height=300, min_width=500, legend=False, yformatter='%.0f', responsive=True).opts(xlabel="Most Common Fuel Type in Census Tract", ylabel="Tracts with Specified Energy Burden", title= "Energy Burden by Fuel Type")

   

In [33]:
@pn.depends(Burden.param.value_throttled)
def plot_bar5(Burden):
        Burden_df = Data[Data['EnergyBurden'] == Burden]
        df = pd.DataFrame(Burden_df.groupby('Utilities')[['Utilities','OBJECTID']]
                      .count()['OBJECTID'])
        df['Utilities'] = df.index
        return df.hvplot.bar(x='Utilities', y='OBJECTID', c='Utilities', cmap='viridis', min_height=300, min_width=500, legend=False, yformatter='%.0f', responsive=True).opts(xlabel="Most Common Utilities Payment in Census Tract", ylabel="Tracts with Specified Energy Burden", title= "Energy Burden by Utility Payment")
    
    

In [34]:
def plot_bar6():
        df = pd.DataFrame(Data.groupby('EnergyBurden')[['EnergyBurden','HouseholdCount']]
                      .count()['HouseholdCount'])
        df['EnergyBurden'] = df.index
        return df.hvplot.bar(x='EnergyBurden', y='HouseholdCount', c='EnergyBurden', cmap='viridis', min_height=350, min_width=600, legend=False, yformatter='%.0f', responsive=True).opts(xlabel="Energy Burden (% of Income)", ylabel="Count of Households", title = "Households Energy Burdens")

In [35]:
@pn.depends(Burden.param.value_throttled)
def plot_bar7(Burden):
        Burden_df = Data[Data['EnergyBurden'] == Burden]
        df = pd.DataFrame(Burden_df.groupby('IncomeLevel')[['IncomeLevel','OBJECTID']]
                      .count()['OBJECTID'])
        df['IncomeLevel'] = df.index
        return df.hvplot.bar(x='IncomeLevel', y='OBJECTID', c='IncomeLevel', cmap='viridis', min_height=300, min_width=500, legend=False, yformatter='%.0f', responsive=True).opts(xlabel="Median Income", ylabel="Tracts with Specified Energy Burden", title= "Energy Burden by Income Level (Area Median Income)")

## Putting it all together

In [36]:
class EnergyBurdenByTract(pm.Parameterized):
    pn.extension(sizing_mode='fixed')
    Burden = pn.widgets.IntSlider(name='Energy Burden (% of Income) Slider', width = 200, start = 1, end =10, value = (5), step=1, value_throttled= (3))
    
    @pn.depends(Burden.param.value_throttled)
    def Burden_selected(Burden):
        return 'Average Energy Burden = {}'.format(Burden)
    
    @pn.depends(Burden.param.value_throttled)
    def plot_bar1(Burden):
        Burden_df = Data[Data['EnergyBurden'] == Burden]
        df = pd.DataFrame(Burden_df.groupby('Race')[['Race','OBJECTID']]
                      .count()['OBJECTID'])
        df['Race'] = df.index
        return df.hvplot.bar(x='Race', y='OBJECTID', c='Race', cmap='viridis', min_height=300, min_width=500, legend=False, yformatter='%.0f', responsive=True).opts(xlabel="Most Common Race in Census Tract", ylabel="Tracts with Specified Energy Burden", title= "Energy Burden by Race")

    @pn.depends(Burden.param.value_throttled)
    def plot_bar2(Burden):
        Burden_df = Data[Data['EnergyBurden'] == Burden]
        df = pd.DataFrame(Burden_df.groupby('Housing')[['Housing','OBJECTID']]
                      .count()['OBJECTID'])
        df['Housing'] = df.index
        return df.hvplot.bar(x='Housing', y='OBJECTID', c='Housing', cmap='viridis', min_height=300, min_width=500, legend=False, yformatter='%.0f', responsive=True).opts(xlabel="Most Common Housing Type in Census Tract", ylabel="Tracts with Specified Energy Burden", title= "Energy Burden by Housing Type")

    @pn.depends(Burden.param.value_throttled)
    def plot_bar3(Burden):
        Burden_df = Data[Data['EnergyBurden'] == Burden]
        df = pd.DataFrame(Burden_df.groupby('Occupancy')[['Occupancy','OBJECTID']]
                        .count()['OBJECTID'])
        df['Occupancy'] = df.index
        return df.hvplot.bar(x='Occupancy', y='OBJECTID', c='Occupancy', cmap='viridis', min_height=300, min_width=500, legend=False, yformatter='%.0f', responsive=True).opts(xlabel="Most Common Occupancy Type in Census Tract", ylabel="Tracts with Specified Energy Burden", title= "Energy Burden by Occupancy Type")

    @pn.depends(Burden.param.value_throttled)
    def plot_bar4(Burden):
        Burden_df = Data[Data['EnergyBurden'] == Burden]
        df = pd.DataFrame(Burden_df.groupby('Fuel')[['Fuel','OBJECTID']]
                      .count()['OBJECTID'])
        df['Fuel'] = df.index
        return df.hvplot.bar(x='Fuel', y='OBJECTID', c='Fuel', cmap='viridis', min_height=300, min_width=500, legend=False, yformatter='%.0f', responsive=True).opts(xlabel="Most Common Fuel Type in Census Tract", ylabel="Tracts with Specified Energy Burden", title= "Energy Burden by Fuel Type")

    @pn.depends(Burden.param.value_throttled)
    def plot_bar5(Burden):
        Burden_df = Data[Data['EnergyBurden'] == Burden]
        df = pd.DataFrame(Burden_df.groupby('Utilities')[['Utilities','OBJECTID']]
                      .count()['OBJECTID'])
        df['Utilities'] = df.index
        return df.hvplot.bar(x='Utilities', y='OBJECTID', c='Utilities', cmap='viridis', min_height=300, min_width=500, legend=False, yformatter='%.0f', responsive=True).opts(xlabel="Most Common Utilities Payment in Census Tract", ylabel="Tracts with Specified Energy Burden", title= "Energy Burden by Utility Payment")
    
    def plot_bar6():
        df = pd.DataFrame(Data.groupby('EnergyBurden')[['EnergyBurden','HouseholdCount']]
                      .count()['HouseholdCount'])
        df['EnergyBurden'] = df.index
        return df.hvplot.bar(x='EnergyBurden', y='HouseholdCount', c='EnergyBurden', cmap='viridis', min_height=350, min_width=600, legend=False, yformatter='%.0f', responsive=True).opts(xlabel="Energy Burden (% of Income)", ylabel="Count of Households", title = "Households Energy Burdens")
    
    @pn.depends(Burden.param.value_throttled)
    def plot_bar7(Burden):
        Burden_df = Data[Data['EnergyBurden'] == Burden]
        df = pd.DataFrame(Burden_df.groupby('IncomeLevel')[['IncomeLevel','OBJECTID']]
                      .count()['OBJECTID'])
        df['IncomeLevel'] = df.index
        return df.hvplot.bar(x='IncomeLevel', y='OBJECTID', c='IncomeLevel', cmap='viridis', min_height=300, min_width=500, legend=False, yformatter='%.0f', responsive=True).opts(xlabel="Median Income", ylabel="Tracts with Specified Energy Burden", title= "Energy Burden by Income Level (Area Median Income)")
    
    def choropleth():
        columns2 = ["GEOID", "NAME", "geometry", "EnergyBurden","HouseholdCount","MedianMonthlyHousingCosts", "AvgAnnualEnergyCost","Rent%Income"]
        return Data[columns2].hvplot.polygons(
            c="EnergyBurden",
            legend=True,
            cmap="viridis",
            hover_cols=["NAME", "GEOID", "EnergyBurden", "HouseholdCount", "MedianMonthlyHousingCosts", "AvgAnnualEnergyCost", "Rent%Income"],
            frame_width=550,
            frame_height=600,
            geo=True,
            crs=3857,
            title="Average Energy Burden by Census Tracts"
        )

## Build app

In [37]:
app = EnergyBurdenByTract(name="")

In [41]:
title = pn.Pane("<h1>Exploring Philadelphia Energy Burdens</h1>", width=1000)
sumtext = pn.Pane("<h4>This dashboard allows users to examine energy burdens, the percent of income spent on energy costs, across the city. Use the slider to breakdown the different characteristics of households with your specified energy burden. Data is collected from OpenDataPhilly, U.S. Census Bureau, and U.S. Department of Energy. </h4>", width=1000)

In [42]:
plots_box = pn.WidgetBox(pn.Column(pn.Row(Burden_selected, Burden)
                                  ,pn.Row(pn.bind(plot_bar7, Burden),
                                         pn.bind(plot_bar1,Burden)), pn.Row(pn.bind(plot_bar2,Burden), pn.bind(plot_bar3,Burden)), pn.Row(pn.bind(plot_bar5,Burden), pn.bind(plot_bar4,Burden)), align="start", sizing_mode="stretch_width"))
mapbox = pn.Column(pn.bind(choropleth),pn.bind(plot_bar6), align=("end", "start"), sizing_mode="stretch_height")
titlebox = pn.Column(title, sumtext)

panel = pn.Column(pn.Row(titlebox),pn.Row(plots_box, mapbox, align=("end", "start"), sizing_mode="scale_both"))

In [43]:
panel.servable()

C:\Users\admin\miniconda3\envs\musa-550-fall-2022\lib\site-packages\geoviews\operation\projection.py:79: ShapelyDeprecationWarning: Iteration over multi-part geometries is deprecated and will be removed in Shapely 2.0. Use the `geoms` property to access the constituent parts of a multi-part geometry.
  polys = [g for g in geom if g.area > 1e-15]


Column(sizing_mode='fixed')
    [0] Row(sizing_mode='fixed')
        [0] Column(sizing_mode='fixed')
            [0] Markdown(str, sizing_mode='fixed', width=1000)
            [1] Markdown(str, sizing_mode='fixed', width=1000)
    [1] Row(align=('end', 'start'), sizing_mode='scale_both')
        [0] WidgetBox(sizing_mode='fixed')
            [0] Column(sizing_mode='stretch_width')
                [0] Row(sizing_mode='fixed')
                    [0] ParamFunction(function, sizing_mode='fixed')
                    [1] IntSlider(end=10, name='Energy Burden (..., sizing_mode='fixed', start=1, value=5, width=200)
                [1] Row(sizing_mode='fixed')
                    [0] ParamFunction(function, sizing_mode='fixed')
                    [1] ParamFunction(function, sizing_mode='fixed')
                [2] Row(sizing_mode='fixed')
                    [0] ParamFunction(function, sizing_mode='fixed')
                    [1] ParamFunction(function, sizing_mode='fixed')
                [3] Row(sizing_mode='fixed')
                    [0] ParamFunction(function, sizing_mode='fixed')
                    [1] ParamFunction(function, sizing_mode='fixed')
        [1] Column(align=('end', 'start'), sizing_mode='stretch_height')
            [0] ParamFunction(function, sizing_mode='fixed')
            [1] ParamFunction(function, sizing_mode='fixed')